In [1]:
import requests, numpy as np, pandas as pd, datetime as dt
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.arima.model import ARIMA
from pmdarima import auto_arima
import concurrent.futures

# Set globals
API_KEY = 'fbf2a3cac76ec733ee2b8c01ab036950'
URL_BASE = 'https://api.stlouisfed.org/fred/series/observations'
START = pd.Timestamp('1983-01-01').date()
END = pd.Timestamp('2022-12-31').date()
BUSDAYS_IN_RANGE = np.busday_count(START, END)
META_INDEX = ['observation_start', 'observation_end', 'busdays_in_range', 'actual_start', 'actual_end', 'actual_days', 'nan_count']
SERIES_LIST = ['DEXUSUK', 'DEXCAUS', 'DEXCHUS', 'DEXJPUS', 'DEXINUS', 'DEXSFUS']
CCY_LIST = ['GBP', 'CAD', 'CNY', 'JPY', 'INR', 'ZAR']

# Create function to get raw json return from FRED database
def get_series_json(series_id, start, end, api_key=API_KEY, file_type='json', url_base=URL_BASE):
    url = f'{url_base}?series_id={series_id}&observation_start={start}&observation_end={end}'
    url += f'&api_key={api_key}&file_type={file_type}'
    try:
        resp = requests.get(url)
        resp.raise_for_status()  # Raise exception if invalid response
        return resp
    except Exception as e:
        errmsg = resp.json()['error_message'].replace('series', f'series {series_id}')
        print(f'Error: {resp.status_code}\n{errmsg}')
        return None

# Create function to transform valid json response from FRED into a dataframe
def transform_series_json(resp, series_id):
    resp = resp.json()
    obs = pd.DataFrame(resp.pop('observations'))[['date', 'value']]
    obs['date'] = pd.to_datetime(obs['date'])
    obs.set_index('date', inplace=True)
    meta = pd.DataFrame({
        series_id: {'observation_start': resp['observation_start'],
            'observation_end': resp['observation_end'],
            'busdays_in_range': BUSDAYS_IN_RANGE,
            'actual_days': resp['count'],
            'actual_start': obs.index.min().date(),
            'actual_end': obs.index.max().date(),
            'nan_count': obs[obs.value == '.'].count().value}})
    meta = meta.reindex(META_INDEX)
    obs.loc[obs.value == '.'] = np.nan
    obs.columns = [series_id]
    obs[series_id] = obs[series_id].astype(float, errors='raise')
    return obs, meta

# Create function to fill missing values in FRED series datafame
def fill_series_na(df):
    df.fillna(method='ffill', inplace=True)  # Fill missing values with last observation
    df.fillna(method='bfill', inplace=True)  # Then, fill with next observation
    return df

# Create a function to get a time series from FRED and return a clean dataframe
def get_series(series_id, start, end, api_key=API_KEY, file_type='json', fill_na=None):
    fill_na = True if fill_na is None else fill_na  # Default
    try:
        resp = get_series_json(series_id=series_id, start=start, end=end, api_key=api_key, file_type=file_type)
        df, meta = transform_series_json(resp, series_id=series_id)
        df = fill_series_na(df) if fill_na else df
    except Exception as e:
        print(f'Error retrieving {series_id}.\n{e}')
        return None
    return df, meta

# Convenience function to get multiple series at once
def get_multiple_series(series_list, start, end, fill_na=None):
    fill_na = True if fill_na is None else fill_na  # Default
    df_list = []
    meta_list = []
    for series in series_list:
        df, meta = get_series(series_id=series, start=start, end=end)
        df_list.append(df)
        meta_list.append(meta)
    dfs = pd.concat(df_list, axis=1)
    metas = pd.concat(meta_list, axis=1)
    
    print(f'\nDownloaded {len(df_list)} / {len(series_list)} series') 
    print(f'\nMeta Info on downloaded series: \n{metas.to_markdown()}')
    print(f'\nCombined series dataframe: \n{dfs.set_index(dfs.index.date).head().to_markdown()}')
    return dfs, metas

In [2]:
dfs, metas = get_multiple_series(series_list=SERIES_LIST, start=START, end=END, fill_na=True)


Downloaded 6 / 6 series

Meta Info on downloaded series: 
|                   | DEXUSUK    | DEXCAUS    | DEXCHUS    | DEXJPUS    | DEXINUS    | DEXSFUS    |
|:------------------|:-----------|:-----------|:-----------|:-----------|:-----------|:-----------|
| observation_start | 1983-01-01 | 1983-01-01 | 1983-01-01 | 1983-01-01 | 1983-01-01 | 1983-01-01 |
| observation_end   | 2022-12-31 | 2022-12-31 | 2022-12-31 | 2022-12-31 | 2022-12-31 | 2022-12-31 |
| busdays_in_range  | 10435      | 10435      | 10435      | 10435      | 10435      | 10435      |
| actual_start      | 1983-01-03 | 1983-01-03 | 1983-01-03 | 1983-01-03 | 1983-01-03 | 1983-01-03 |
| actual_end        | 2022-12-30 | 2022-12-30 | 2022-12-30 | 2022-12-30 | 2022-12-30 | 2022-12-30 |
| actual_days       | 10435      | 10435      | 10435      | 10435      | 10435      | 10435      |
| nan_count         | 395        | 395        | 456        | 395        | 403        | 404        |

Combined series dataframe: 
|           

In [3]:
dfs.describe()

DEXUSUK       DEXCAUS       DEXCHUS       DEXJPUS       DEXINUS  \
count  10435.000000  10435.000000  10435.000000  10435.000000  10435.000000   
mean       1.568031      1.270046      6.442683    124.002514     42.280554   
std        0.196309      0.151302      1.823216     37.191829     19.472289   
min        1.052000      0.916800      1.894900     75.720000      9.620000   
25%        1.438400      1.165650      5.724300    105.600000     29.000000   
50%        1.567700      1.285700      6.737000    114.030000     44.150000   
75%        1.671650      1.368000      8.276700    128.645000     54.925000   
max        2.110400      1.612800      8.740900    262.800000     82.950000   

            DEXSFUS  
count  10435.000000  
mean       7.238724  
std        4.477897  
min        1.061000  
25%        3.055250  
50%        6.760800  
75%       10.214000  
max       19.040000

In [4]:
dfs.head()

DEXUSUK  DEXCAUS  DEXCHUS  DEXJPUS  DEXINUS  DEXSFUS
date                                                            
1983-01-03   1.6235   1.2300   1.9275    232.0     9.62   1.0695
1983-01-04   1.6210   1.2298   1.9140    229.8     9.64   1.0667
1983-01-05   1.6210   1.2297   1.9140    229.1     9.64   1.0684
1983-01-06   1.6065   1.2313   1.9044    229.8     9.70   1.0712
1983-01-07   1.6100   1.2267   1.9044    229.1     9.73   1.0712

In [5]:
rates = dfs.copy()
rates.columns = CCY_LIST
rates.index.freq = 'B'
aligned = dfs.copy()
aligned.iloc[:, 1:] = aligned.iloc[:, 1:].rdiv(1)
aligned.head()

DEXUSUK   DEXCAUS   DEXCHUS   DEXJPUS   DEXINUS   DEXSFUS
date                                                                 
1983-01-03   1.6235  0.813008  0.518807  0.004310  0.103950  0.935016
1983-01-04   1.6210  0.813140  0.522466  0.004352  0.103734  0.937471
1983-01-05   1.6210  0.813206  0.522466  0.004365  0.103734  0.935979
1983-01-06   1.6065  0.812150  0.525100  0.004352  0.103093  0.933532
1983-01-07   1.6100  0.815195  0.525100  0.004365  0.102775  0.933532

In [6]:
layout = {'title': '<b>Currency 40-Year Daily Rates</b><br><sup><i>(1983-2022)</i></sup>',
          'width': 1800,
          'height': 800,
          'template': 'seaborn',
          'hovermode': 'x unified'}
def plot_all_rates(df, layout, x_title, y_title, ht, yshared=False):
    fig = make_subplots(rows=2, cols=3, shared_xaxes=True, vertical_spacing=0.05, horizontal_spacing=0.02,
                        subplot_titles=([ccy for ccy in df]), shared_yaxes=yshared, x_title=x_title, y_title=y_title)
    for i, ccy in enumerate(df):
        trace = go.Scatter(x=df.index, y=df[ccy], mode='lines', name=ccy, hovertemplate=ht)
        if i // 3 < 1:
            fig.add_trace(trace, row=1, col=i+1)
        else:
            fig.add_trace(trace, row=2, col=i-2)
    fig.update_layout(layout)
    return fig

x_title = 'Date 1983-2022'
y_title = 'Daily Rate Against US Dollar<br><sup><i>Except in the case of GBP which is reverse</i></sup>'
rate_fig = plot_all_rates(df=rates, layout=layout, x_title=x_title, y_title=y_title, ht='%{y:,.1%}')
rate_fig.show()

In [7]:
def plot_all_hist(df, layout, x_title, y_title, ht, yshared=False):
    fig = make_subplots(rows=2, cols=3, shared_xaxes=False, vertical_spacing=0.05, horizontal_spacing=0.02,
                        subplot_titles=([ccy for ccy in df]), shared_yaxes=yshared, x_title=x_title, y_title=y_title)
    for i, ccy in enumerate(df):
        trace = go.Histogram(x=rates[ccy], name=ccy, nbinsx=25)
        if i // 3 < 1:
            fig.add_trace(trace, row=1, col=i+1)
        else:
            fig.add_trace(trace, row=2, col=i-2)
    fig.update_layout(layout)
    return fig

x_title = 'Date 1983-2022'
y_title = 'Histogram of Daily Rates Against US Dollar'
hist_fig = plot_all_hist(df=rates, layout=layout, x_title=x_title, y_title=y_title, ht='%{y}')
hist_fig.show()

In [8]:
aligned_diff = aligned.pct_change().dropna().add(1).cumprod()
aligned_diff.tail()

DEXUSUK   DEXCAUS   DEXCHUS   DEXJPUS   DEXINUS   DEXSFUS
date                                                                  
2022-12-26  0.742470  0.905277  0.275830  1.747251  0.116099  0.063014
2022-12-27  0.741115  0.910841  0.276940  1.738739  0.116071  0.061810
2022-12-28  0.741238  0.905210  0.276249  1.727862  0.116268  0.062489
2022-12-29  0.742840  0.908017  0.276840  1.742265  0.116141  0.063321
2022-12-30  0.743887  0.908957  0.279461  1.760109  0.116296  0.062930

In [9]:
layout['title'] = '<b>Currency 40-Year Cumulative Percentage Change</b><br><sup><i>(1983-2022)</i></sup>'
x_title = 'Date 1983-2022'
y_title = 'Cumulative Foreign Currency Rate Percentage Change VS US Dollar'
diff_fig = plot_all_rates(df=aligned_diff, layout=layout, x_title=x_title, y_title=y_title, ht='%{y:,.2f}', yshared=True)
diff_fig.show()

In [10]:
def plot_seasonal(series, resample=None):
    if resample is not None:
        series = series.resample(resample).mean()
    decomp = seasonal_decompose(series)
    decomp_fig = make_subplots(rows=4, cols=1, shared_xaxes=True)
    decomp_fig.add_trace(go.Scatter(x=decomp.observed.index, y=decomp.observed.values, name='Observed'), row=1, col=1)
    decomp_fig.add_trace(go.Scatter(x=decomp.trend.index, y=decomp.trend.values, name='Trend'), row=2, col=1)
    decomp_fig.add_trace(go.Scatter(x=decomp.seasonal.index, y=decomp.seasonal.values, name='Seasonal'), row=3, col=1)
    decomp_fig.add_trace(go.Scatter(x=decomp.resid.index, y=decomp.resid.values, name='Residuals'), row=4, col=1)
    decomp_fig.update_layout(width=1800, height=800, title=f'{series.name} Seasonal Decomposition Plot', template='seaborn')
    ynames = ['Observed', 'Trend', 'Seasonal', 'Residuals']
    for i, name in enumerate(ynames):
        decomp_fig.update_yaxes(title_text=name, row=i+1)
    return decomp_fig

def multi_plot_seasonal(df, resample=None):
    if resample is not None:
        df = df.resample(resample).mean()
    ncols = df.shape[1]
    decomp_fig = make_subplots(rows=4, cols=ncols, subplot_titles=df.columns, shared_xaxes=True, 
                               vertical_spacing=0.01, horizontal_spacing=0.03)
    for col in df:
        decomp = seasonal_decompose(df[col])
        figcol = df.columns.get_loc(col) + 1
        decomp_fig.add_trace(go.Scatter(x=decomp.observed.index, y=decomp.observed.values, name=f'{col}: Observed'), row=1, col=figcol)
        decomp_fig.add_trace(go.Scatter(x=decomp.trend.index, y=decomp.trend.values, name=f'{col}: Trend'), row=2, col=figcol)
        decomp_fig.add_trace(go.Scatter(x=decomp.seasonal.index, y=decomp.seasonal.values, name=f'{col}: Seasonal'), row=3, col=figcol)
        decomp_fig.add_trace(go.Scatter(x=decomp.resid.index, y=decomp.resid.values, name=f'{col}: Residuals'), row=4, col=figcol)
    decomp_fig.update_layout(width=2200, height=800, title='Seasonal Decomposition Plot', template='seaborn', showlegend=False)
    ynames = ['Observed', 'Trend', 'Seasonal', 'Residuals']
    for i, name in enumerate(ynames):
        decomp_fig.update_yaxes(title_text=name, row=i+1, col=1)
        decomp_fig.update_yaxes(tickformat='.1f')
    return decomp_fig

multiplot = multi_plot_seasonal(rates, resample='M')
multiplot.show()

In [11]:
# Build train/test split 
end = rates.index[-1]
start = end - dt.timedelta(days=90)
# start = rates.index[rates.index.get_indexer([start], method='nearest')][0]
end = rates.index[rates.index.get_indexer([start], method='nearest')][0]
start = rates.index[rates.index.get_indexer([start], method='nearest') + 1][0]
# trains = rates.loc[:start].copy()
trains = rates.loc[:end].copy()
tests = rates.loc[start:].copy()

arimafits = {}
with concurrent.futures.ProcessPoolExecutor(max_workers=8) as executor:
    future_to_arima = {executor.submit(auto_arima, trains[ccy]): ccy for ccy in trains}
    for future in concurrent.futures.as_completed(future_to_arima):
        ccy = future_to_arima[future]
        try:
            arimafits[ccy] = future.result()
        except Exception as e:
            print(f'{ccy} generated an exception: {e}')
        else:
            print(f'{ccy} ARIMA Summary:\n{arimafits[ccy].summary().as_text()}\n\n{"-"*100}')

CAD ARIMA Summary:
                               SARIMAX Results                                
Dep. Variable:                      y   No. Observations:                10370
Model:               SARIMAX(0, 1, 0)   Log Likelihood               39169.407
Date:                Mon, 21 Aug 2023   AIC                         -78336.814
Time:                        20:48:42   BIC                         -78329.567
Sample:                    01-03-1983   HQIC                        -78334.366
                         - 09-30-2022                                         
Covariance Type:                  opg                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
sigma2      3.064e-05    1.9e-07    160.983      0.000    3.03e-05     3.1e-05
Ljung-Box (L1) (Q):                   1.27   Jarque-Bera (JB):             27663.45
Prob(Q):                    

In [12]:
layout = {'title': 'Currency Rate 90-Day Forecast',
          'width': 2000,
          'height': 1200,
          'template': 'seaborn',
          'hovermode': 'x unified'}

hovertemp = '%{y:,.4f}'

def plot_all_forecasts(trains, arimafits, layout, x_title, y_title, historical, sma, sma_df):
    fcfig = make_subplots(rows=2, cols=3, shared_xaxes=True, vertical_spacing=0.05, horizontal_spacing=0.02, 
                          subplot_titles=([ccy for ccy in trains]), shared_yaxes=False, x_title=x_title, y_title=y_title)
    for i, ccy in enumerate(trains):
        train = trains[ccy]
        test = tests[ccy]
        year = str(trains.index[-1].year)
        fc = arimafits[ccy].arima_res_.get_prediction(start=train.index[-1], end=test.index[-1]).summary_frame()
        if i // 3 < 1:
            row = 1
            col = i+1
        else:
            row = 2
            col = i-2
        fcfig.add_trace(go.Scatter(name='Forecast', x=fc.index, y=fc['mean'], mode='lines', line=dict(color='#e66830'), showlegend=False,
                                   hovertemplate=hovertemp), row=row, col=col)
        fcfig.add_trace(go.Scatter(name='Upper CI', x=fc.index, y=fc['mean_ci_upper'], line=dict(width=0), mode='lines', showlegend=False,
                                   hovertemplate=hovertemp), row=row, col=col)
        fcfig.add_trace(go.Scatter(name='Lower CI', x=fc.index, y=fc['mean_ci_lower'], marker=dict(color="#444"), line=dict(width=0), mode='lines', 
                                   fillcolor='rgba(66, 107, 133, 0.3)', fill='tonexty', showlegend=False, hovertemplate=hovertemp), row=row, col=col)
        fcfig.add_trace(go.Scatter(name='Actual', x=test.index, y=test, mode='lines', line=dict(color='#00b2c9'), hovertemplate=hovertemp, 
                                   showlegend=False), row=row, col=col)
        if historical:
            fcfig.add_trace(go.Scatter(name='Historical', x=train.loc[year].index, y=train.loc[year], mode='lines', line=dict(color='#200040'),
                                       showlegend=False, hovertemplate=hovertemp), row=row, col=col)
        if sma:
            fcfig.add_trace(go.Scatter(name='SMA', x=sma_df.index, y=sma_df[ccy], mode='lines', line=dict(color='#d3de00'), hovertemplate=hovertemp, 
                                       showlegend=False), row=row, col=col)
        
    fcfig.update_layout(layout)
    return fcfig
    
fcfig = plot_all_forecasts(trains, arimafits, layout, x_title='Date range for 2022 year', 
                           y_title='Daily Rate Against US Dollar<br><sup><i>with forecast, actual, and upper/lower confidence bounds for last 90-days</i></sup>',
                           historical=True, sma=False, sma_df=None)
fcfig.show()

In [13]:
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_percentage_error


# Create function to evaluate forecasts using MSE, RMSE, and MAPE
def eval_forecasts(preds, tests, arima):
    eval_results = {}
    metric = ['MSE', 'RMSE', 'Mean Act', 'RMSE / Mean Act', 'MAPE']
    for ccy in preds:
        if arima:
            pred = preds[ccy].arima_res_.get_prediction(start=tests.index[0], end=tests.index[-1])._predicted_mean
        else:
            pred = preds[ccy]
        act = tests[ccy]
        mse = mean_squared_error(act, pred)
        rmse = mean_squared_error(act, pred, squared=False)  # squared=False actually returns RMSE as default is MSE (squared=True)
        mape = mean_absolute_percentage_error(act, pred)  # Mean Absolute Percentage Error
        results = [mse, rmse, act.mean(), rmse / act.mean(), mape]
        eval_results[ccy] = results
    return pd.DataFrame(eval_results, index=metric).T.sort_values('MAPE', ascending=False)
    
md_formats = (',.4f', ',.4f', ',.4f', ',.4f', ',.2%', '.2%')
arima_eval = eval_forecasts(preds=arimafits, tests=tests, arima=True)
print(f'ARIMA Evaluation:\n{arima_eval.to_markdown(floatfmt=md_formats)}')

ARIMA Evaluation:
|     |      MSE |    RMSE |   Mean Act |   RMSE / Mean Act |   MAPE |
|:----|---------:|--------:|-----------:|------------------:|-------:|
| JPY | 240.7251 | 15.5153 |   141.2715 |            10.98% |  8.81% |
| GBP |   0.0053 |  0.0729 |     1.1752 |             6.21% |  5.14% |
| ZAR |   0.5203 |  0.7213 |    17.5994 |             4.10% |  3.47% |
| CNY |   0.0605 |  0.2460 |     7.1119 |             3.46% |  3.19% |
| CAD |   0.0005 |  0.0223 |     1.3574 |             1.65% |  1.38% |
| INR |   0.6124 |  0.7826 |    82.1385 |             0.95% |  0.82% |


In [14]:
ma_window = 90
sma = rates.rolling(ma_window).mean()
sma = sma.loc[start:]

layout['title'] = 'Currency Rate 90-Day Forecast with 90-Day SMA'

fcfig = plot_all_forecasts(trains, arimafits, layout, x_title='Date range for 2022 year', 
                           y_title='Daily Rate Against US Dollar<br><sup><i>with forecast, Simple Moving Average actual, and upper/lower confidence bounds for last 90-days</i></sup>',
                           historical=False, sma=True, sma_df=sma)
fcfig.show()

In [15]:
sma_eval = eval_forecasts(sma, tests, arima=False)
print(f'ARIMA Evaluation: \n{arima_eval.to_markdown(floatfmt=md_formats)}')
print(f'SMA Evaluation: \n{sma_eval.to_markdown(floatfmt=md_formats)}')


ARIMA Evaluation: 
|     |      MSE |    RMSE |   Mean Act |   RMSE / Mean Act |   MAPE |
|:----|---------:|--------:|-----------:|------------------:|-------:|
| JPY | 240.7251 | 15.5153 |   141.2715 |            10.98% |  8.81% |
| GBP |   0.0053 |  0.0729 |     1.1752 |             6.21% |  5.14% |
| ZAR |   0.5203 |  0.7213 |    17.5994 |             4.10% |  3.47% |
| CNY |   0.0605 |  0.2460 |     7.1119 |             3.46% |  3.19% |
| CAD |   0.0005 |  0.0223 |     1.3574 |             1.65% |  1.38% |
| INR |   0.6124 |  0.7826 |    82.1385 |             0.95% |  0.82% |
SMA Evaluation: 
|     |     MSE |   RMSE |   Mean Act |   RMSE / Mean Act |   MAPE |
|:----|--------:|-------:|-----------:|------------------:|-------:|
| JPY | 45.0085 | 6.7088 |   141.2715 |             4.75% |  4.26% |
| GBP |  0.0022 | 0.0466 |     1.1752 |             3.97% |  3.59% |
| ZAR |  0.5119 | 0.7155 |    17.5994 |             4.07% |  3.21% |
| CNY |  0.0524 | 0.2289 |     7.1119 |            

In [16]:
combined_eval = sma_eval[['MAPE']].merge(arima_eval[['MAPE']], left_index=True, right_index=True, suffixes=('_SMA', '_ARIMA'))
combined_eval['Better Model'] = combined_eval.apply(lambda x: 'SMA' if x['MAPE_SMA'] < x['MAPE_ARIMA'] else 'ARIMA', axis=1)
print(f'Combined Evaluation: \n{combined_eval.to_markdown(floatfmt=".2%")}')

Combined Evaluation: 
|     |   MAPE_SMA |   MAPE_ARIMA | Better Model   |
|:----|-----------:|-------------:|:---------------|
| JPY |      4.26% |        8.81% | SMA            |
| GBP |      3.59% |        5.14% | SMA            |
| ZAR |      3.21% |        3.47% | SMA            |
| CNY |      2.79% |        3.19% | SMA            |
| CAD |      2.24% |        1.38% | ARIMA          |
| INR |      1.89% |        0.82% | ARIMA          |
